## Load library

In [1]:
#python

import json
import copy
import random
import yaml

from datetime import datetime
from typing import Any, Dict, Tuple, Union, List

#automl optuna
import optuna

#numpy

import numpy as np

#pytorch

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision.datasets import ImageFolder

#baseline

import warnings

warnings.filterwarnings('ignore')

import os
import sys

sys.path.append(os.path.dirname(os.path.abspath(os.path.dirname('/opt/ml/code/src/'))))

from src.dataloader import create_dataloader
from src.loss import CustomCriterion
from src.model import Model
from src.trainer import TorchTrainer
from src.utils.common import get_label_counts, read_yaml
from src.utils.macs import calc_macs
from src.utils.torch_utils import check_runtime, model_info
from src.augmentation.policies import simple_augment_test
from src.utils.inference_utils import run_model

from train import train



## hyperparameter

In [4]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

## fixed seed

In [5]:
#torch seed
torch.manual_seed(30)
torch.cuda.manual_seed(30)

#numpy seed
np.random.seed(30)

#python seed
random.seed(30)

## AutoML

## load config

In [6]:
MODEL_CONFIG = read_yaml(cfg="/opt/ml/code/configs/model/mobilenetv3.yaml")
DATA_CONFIG = read_yaml(cfg="/opt/ml/code/configs/data/taco.yaml")

## define hyperparameter search space

In [7]:
def search_hyperparam(trial: optuna.trial.Trial) -> Dict[str, Any]:
    """Search hyperparam from user-specified search space."""
    epochs = trial.suggest_int("epochs", low=50, high=200, step=50)
    img_size = trial.suggest_categorical("img_size", [16,32,48,64,96])
    #epochs = 200
    #img_size = 96
    n_select = trial.suggest_int("n_select", low=0, high=6, step=2)
    batch_size = trial.suggest_int("batch_size", low=16, high=64, step=16)
    return {
        "EPOCHS": epochs,
        "IMG_SIZE": img_size,
        "n_select": n_select,
        "BATCH_SIZE": batch_size
    }

## define model architecture search space

In [8]:
def search_model(trial: optuna.trial.Trial) -> List[Any]:
    """Search model structure from user-specified search space."""
    model = []
    # 1, 2,3, 4,5, 6,7, 8,9
    # TODO: remove hard-coded stride
    n_stride = 0
    MAX_NUM_STRIDE = 5
    UPPER_STRIDE = 2 # 5(224 example): 224, 112, 56, 28, 14, 7

    # Module 1
    m1 = trial.suggest_categorical("m1", ["Conv", "DWConv"])
    m1_args = []
    m1_repeat = trial.suggest_int("m1/repeat", 1, 3)
    m1_out_channel = trial.suggest_int("m1/out_channels", low=16, high=64, step=16)
    m1_stride = trial.suggest_int("m1/stride", low=1, high=UPPER_STRIDE)
    if m1_stride == 2:
        n_stride += 1
    m1_activation = trial.suggest_categorical(
        "m1/activation", ["ReLU", "Hardswish"]
        )
    if m1 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m1_args = [m1_out_channel, 3, m1_stride, None, 1, m1_activation]
    elif m1 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m1_args = [m1_out_channel, 3, m1_stride, None, m1_activation]
    model.append([m1_repeat, m1, m1_args])

    # Module 2
    m2 = trial.suggest_categorical(
        "m2",
        ["Conv",
        "DWConv",
        "InvertedResidualv2",
        "InvertedResidualv3",
        "Pass"]
        )
    m2_args = []
    m2_repeat = trial.suggest_int("m2/repeat", 1, 5)
    m2_out_channel = trial.suggest_int("m2/out_channels", low=16, high=128, step=16)
    m2_stride = trial.suggest_int("m2/stride", low=1, high=UPPER_STRIDE)
    # force stride m2
    if n_stride == 0:
        m2_stride = 2
    if m2 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m2_kernel = trial.suggest_int("m2/kernel_size", low=1, high=5, step=2)
        m2_activation = trial.suggest_categorical("m2/activation", ["ReLU", "Hardswish"])
        m2_args = [m2_out_channel, m2_kernel, m2_stride, None, 1, m2_activation]
    elif m2 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m2_kernel = trial.suggest_int("m2/kernel_size", low=1, high=5, step=2)
        m2_activation = trial.suggest_categorical("m2/activation", ["ReLU", "Hardswish"])
        m2_args = [m2_out_channel, m2_kernel, m2_stride, None, m2_activation]
    elif m2 == "InvertedResidualv2":
        m2_c = trial.suggest_int("m2/v2_c", low=16, high=32, step=16)
        m2_t = trial.suggest_int("m2/v2_t", low=1, high=4)
        m2_args = [m2_c, m2_t, m2_stride]
    elif m2 == "InvertedResidualv3":
        m2_kernel = trial.suggest_int("m2/kernel_size", low=3, high=5, step=2)
        m2_t = round(trial.suggest_float("m2/v3_t", low=1.0, high=6.0, step=0.1), 1)
        m2_c = trial.suggest_int("m2/v3_c", low=16, high=40, step=8)
        m2_se = trial.suggest_categorical("m2/v3_se", [0, 1])
        m2_hs = trial.suggest_categorical("m2/v3_hs", [0, 1])
        # k t c SE HS s
        m2_args = [m2_kernel, m2_t, m2_c, m2_se, m2_hs, m2_stride]
    if not m2 == "Pass":
        if m2_stride == 2:
            n_stride += 1
            if n_stride>=MAX_NUM_STRIDE:
                UPPER_STRIDE = 1
        model.append([m2_repeat, m2, m2_args])

    # Module 3
    m3 = trial.suggest_categorical(
        "m3",
        ["Conv",
        "DWConv",
        "InvertedResidualv2",
        "InvertedResidualv3",
        "Pass"]
        )
    m3_args = []
    m3_repeat = trial.suggest_int("m3/repeat", 1, 5)
    m3_stride = trial.suggest_int("m3/stride", low=1, high=UPPER_STRIDE)
    if m3 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m3_out_channel = trial.suggest_int("m3/out_channels", low=16, high=128, step=16)
        m3_kernel = trial.suggest_int("m3/kernel_size", low=1, high=5, step=2)
        m3_activation = trial.suggest_categorical("m3/activation", ["ReLU", "Hardswish"])
        m3_args = [m3_out_channel, m3_kernel, m3_stride, None, 1, m3_activation]
    elif m3 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m3_out_channel = trial.suggest_int("m3/out_channels", low=16, high=128, step=16)
        m3_kernel = trial.suggest_int("m3/kernel_size", low=1, high=5, step=2)
        m3_activation = trial.suggest_categorical("m3/activation", ["ReLU", "Hardswish"])
        m3_args = [m3_out_channel, m3_kernel, m3_stride, None, m3_activation]
    elif m3 == "InvertedResidualv2":
        m3_c = trial.suggest_int("m3/v2_c", low=8, high=32, step=8)
        m3_t = trial.suggest_int("m3/v2_t", low=1, high=8)
        m3_args = [m3_c, m3_t, m3_stride]
    elif m3 == "InvertedResidualv3":
        m3_kernel = trial.suggest_int("m3/kernel_size", low=3, high=5, step=2)
        m3_t = round(trial.suggest_float("m3/v3_t", low=1.0, high=6.0, step=0.1), 1)
        m3_c = trial.suggest_int("m3/v3_c", low=8, high=40, step=8)
        m3_se = trial.suggest_categorical("m3/v3_se", [0, 1])
        m3_hs = trial.suggest_categorical("m3/v3_hs", [0, 1])
        m3_args = [m3_kernel, m3_t, m3_c, m3_se, m3_hs, m3_stride]
    if not m3 == "Pass":
        if m3_stride == 2:
            n_stride += 1
            if n_stride>=MAX_NUM_STRIDE:
                UPPER_STRIDE = 1
        model.append([m3_repeat, m3, m3_args])

    # Module 4
    m4 = trial.suggest_categorical(
        "m4",
        ["Conv",
        "DWConv",
        "InvertedResidualv2",
        "InvertedResidualv3",
        "Pass"]
        )
    m4_args = []
    m4_repeat = trial.suggest_int("m4/repeat", 1, 5)
    m4_stride = trial.suggest_int("m4/stride", low=1, high=UPPER_STRIDE)
    # force stride m4
    if n_stride == 1:
        m4_stride = 2
    if m4 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m4_out_channel = trial.suggest_int("m4/out_channels", low=16, high=256, step=16)
        m4_kernel = trial.suggest_int("m4/kernel_size", low=1, high=5, step=2)
        m4_activation = trial.suggest_categorical("m4/activation", ["ReLU", "Hardswish"])
        m4_args = [m4_out_channel, m4_kernel, m4_stride, None, 1, m4_activation]
    elif m4 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m4_out_channel = trial.suggest_int("m4/out_channels", low=16, high=256, step=16)
        m4_kernel = trial.suggest_int("m4/kernel_size", low=1, high=5, step=2)
        m4_activation = trial.suggest_categorical("m4/activation", ["ReLU", "Hardswish"])
        m4_args = [m4_out_channel, m4_kernel, m4_stride, None, m4_activation]
    elif m4 == "InvertedResidualv2":
        m4_c = trial.suggest_int("m4/v2_c", low=8, high=64, step=8)
        m4_t = trial.suggest_int("m4/v2_t", low=1, high=8)
        m4_args = [m4_c, m4_t, m4_stride]
    elif m4 == "InvertedResidualv3":
        m4_kernel = trial.suggest_int("m4/kernel_size", low=3, high=5, step=2)
        m4_t = round(trial.suggest_float("m4/v3_t", low=1.0, high=6.0, step=0.1), 1)
        m4_c = trial.suggest_int("m4/v3_c", low=8, high=80, step=8)
        m4_se = trial.suggest_categorical("m4/v3_se", [0, 1])
        m4_hs = trial.suggest_categorical("m4/v3_hs", [0, 1])
        m4_args = [m4_kernel, m4_t, m4_c, m4_se, m4_hs, m4_stride]
    if not m4 == "Pass":
        if m4_stride == 2:
            n_stride += 1
            if n_stride>=MAX_NUM_STRIDE:
                UPPER_STRIDE = 1
        model.append([m4_repeat, m4, m4_args])

    # Module 5
    m5 = trial.suggest_categorical(
        "m5",
        ["Conv",
        "DWConv",
        "InvertedResidualv2",
        "InvertedResidualv3",
        "Pass"]
        )
    m5_args = []
    m5_repeat = trial.suggest_int("m5/repeat", 1, 5)
    m5_stride = 1
    if m5 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m5_out_channel = trial.suggest_int("m5/out_channels", low=16, high=256, step=16)
        m5_kernel = trial.suggest_int("m5/kernel_size", low=1, high=5, step=2)
        m5_activation = trial.suggest_categorical("m5/activation", ["ReLU", "Hardswish"])
        m5_stride = trial.suggest_int("m5/stride", low=1, high=UPPER_STRIDE)
        m5_args = [m5_out_channel, m5_kernel, m5_stride, None, 1, m5_activation]
    elif m5 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m5_out_channel = trial.suggest_int("m5/out_channels", low=16, high=256, step=16)
        m5_kernel = trial.suggest_int("m5/kernel_size", low=1, high=5, step=2)
        m5_activation = trial.suggest_categorical("m5/activation", ["ReLU", "Hardswish"])
        m5_stride = trial.suggest_int("m5/stride", low=1, high=UPPER_STRIDE)
        m5_args = [m5_out_channel, m5_kernel, m5_stride, None, m5_activation]
    elif m5 == "InvertedResidualv2":
        m5_c = trial.suggest_int("m5/v2_c", low=16, high=128, step=16)
        m5_t = trial.suggest_int("m5/v2_t", low=1, high=8)
        m5_stride = trial.suggest_int("m5/stride", low=1, high=UPPER_STRIDE)
        m5_args = [m5_c, m5_t, m5_stride]
    elif m5 == "InvertedResidualv3":
        m5_kernel = trial.suggest_int("m5/kernel_size", low=3, high=5, step=2)
        m5_t = round(trial.suggest_float("m5/v3_t", low=1.0, high=6.0, step=0.1), 1)
        m5_c = trial.suggest_int("m5/v3_c", low=16, high=80, step=16)
        m5_se = trial.suggest_categorical("m5/v3_se", [0, 1])
        m5_hs = trial.suggest_categorical("m5/v3_hs", [0, 1])
        m5_stride = trial.suggest_int("m5/stride", low=1, high=UPPER_STRIDE)
        m5_args = [m5_kernel, m5_t, m5_c, m5_se, m5_hs, m5_stride]
    if not m5 == "Pass":
        if m5_stride == 2:
            n_stride += 1
            if n_stride>=MAX_NUM_STRIDE:
                UPPER_STRIDE = 1
        model.append([m5_repeat, m5, m5_args])

    # Module 6
    m6 = trial.suggest_categorical(
        "m6",
        ["Conv",
        "DWConv",
        "InvertedResidualv2",
        "InvertedResidualv3",
        "Pass"]
        )
    m6_args = []
    m6_repeat = trial.suggest_int("m6/repeat", 1, 5)
    m6_stride = trial.suggest_int("m6/stride", low=1, high=UPPER_STRIDE)
    # force stride m6
    if n_stride == 2:
        m4_stride = 2
    if m6 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m6_out_channel = trial.suggest_int("m6/out_channels", low=16, high=512, step=16)
        m6_kernel = trial.suggest_int("m6/kernel_size", low=1, high=5, step=2)
        m6_activation = trial.suggest_categorical("m6/activation", ["ReLU", "Hardswish"])
        m6_args = [m6_out_channel, m6_kernel, m6_stride, None, 1, m6_activation]
    elif m6 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m6_out_channel = trial.suggest_int("m6/out_channels", low=16, high=512, step=16)
        m6_kernel = trial.suggest_int("m6/kernel_size", low=1, high=5, step=2)
        m6_activation = trial.suggest_categorical("m6/activation", ["ReLU", "Hardswish"])
        m6_args = [m6_out_channel, m6_kernel, m6_stride, None, m6_activation]
    elif m6 == "InvertedResidualv2":
        m6_c = trial.suggest_int("m6/v2_c", low=16, high=128, step=16)
        m6_t = trial.suggest_int("m6/v2_t", low=1, high=8)
        m6_args = [m6_c, m6_t, m6_stride]
    elif m6 == "InvertedResidualv3":
        m6_kernel = trial.suggest_int("m6/kernel_size", low=3, high=5, step=2)
        m6_t = round(trial.suggest_float("m6/v3_t", low=1.0, high=6.0, step=0.1), 1)
        m6_c = trial.suggest_int("m6/v3_c", low=16, high=160, step=16)
        m6_se = trial.suggest_categorical("m6/v3_se", [0, 1])
        m6_hs = trial.suggest_categorical("m6/v3_hs", [0, 1])
        m6_args = [m6_kernel, m6_t, m6_c, m6_se, m6_hs, m6_stride]
    if not m6 == "Pass":
        if m6_stride == 2:
            n_stride += 1
            if n_stride>=MAX_NUM_STRIDE:
                UPPER_STRIDE = 1
        model.append([m6_repeat, m6, m6_args])

    # Module 7
    m7 = trial.suggest_categorical(
        "m7",
        ["Conv",
        "DWConv",
        "InvertedResidualv2",
        "InvertedResidualv3",
        "Pass"]
        )
    m7_args = []
    m7_repeat = trial.suggest_int("m7/repeat", 1, 5)
    m7_stride = trial.suggest_int("m7/stride", low=1, high=UPPER_STRIDE)
    if m7 == "Conv":
        # Conv args: [out_channel, kernel_size, stride, padding, groups, activation]
        m7_out_channel = trial.suggest_int("m7/out_channels", low=128, high=1024, step=128)
        m7_kernel = trial.suggest_int("m7/kernel_size", low=1, high=5, step=2)
        m7_activation = trial.suggest_categorical("m7/activation", ["ReLU", "Hardswish"])
        m7_args = [m7_out_channel, m7_kernel, m7_stride, None, 1, m7_activation]
    elif m7 == "DWConv":
        # DWConv args: [out_channel, kernel_size, stride, padding_size, activation]
        m7_out_channel = trial.suggest_int("m7/out_channels", low=128, high=1024, step=128)
        m7_kernel = trial.suggest_int("m7/kernel_size", low=1, high=5, step=2)
        m7_activation = trial.suggest_categorical("m7/activation", ["ReLU", "Hardswish"])
        m7_args = [m7_out_channel, m7_kernel, m7_stride, None, m7_activation]
    elif m7 == "InvertedResidualv2":
        m7_c = trial.suggest_int("m7/v2_c", low=16, high=160, step=16)
        m7_t = trial.suggest_int("m7/v2_t", low=1, high=8)
        m7_args = [m7_c, m7_t, m7_stride]
    elif m7 == "InvertedResidualv3":
        m7_kernel = trial.suggest_int("m7/kernel_size", low=3, high=5, step=2)
        m7_t = round(trial.suggest_float("m7/v3_t", low=1.0, high=6.0, step=0.1), 1)
        m7_c = trial.suggest_int("m7/v3_c", low=8, high=160, step=8)
        m7_se = trial.suggest_categorical("m7/v3_se", [0, 1])
        m7_hs = trial.suggest_categorical("m7/v3_hs", [0, 1])
        m7_args = [m7_kernel, m7_t, m7_c, m7_se, m7_hs, m7_stride]
    if not m7 == "Pass":
        if m7_stride == 2:
            n_stride += 1
            if n_stride>=MAX_NUM_STRIDE:
                UPPER_STRIDE = 1
        model.append([m7_repeat, m7, m7_args])

    # last layer
    last_dim = trial.suggest_int("last_dim", low=128, high=1024, step=128)
    # We can setup fixed structure as well
    model.append([1, "Conv", [last_dim, 1, 1]])
    model.append([1, "GlobalAvgPool", []])
    model.append([1, "FixedConv", [9, 1, 1, None, 1, None]])

    return model


## define objective function

In [9]:
def objective(trial: optuna.trial.Trial, device) -> Tuple[float, int, float]:
    """Optuna objective.

    Args:
        trial
    Returns:
        float: score1(e.g. accuracy)
        int: score2(e.g. params)
    """
    
    global before_macs,success
    
    model_config = copy.deepcopy(MODEL_CONFIG)
    data_config = copy.deepcopy(DATA_CONFIG)

    # hyperparams: EPOCHS, IMG_SIZE, n_select, BATCH_SIZE
    hyperparams = search_hyperparam(trial)

    model_config["input_size"] = [hyperparams["IMG_SIZE"], hyperparams["IMG_SIZE"]]
    model_config["backbone"] = search_model(trial)

    data_config["AUG_TRAIN_PARAMS"]["n_select"] = hyperparams["n_select"]
    data_config["BATCH_SIZE"] = hyperparams["BATCH_SIZE"]
    data_config["EPOCHS"] = hyperparams["EPOCHS"]
    data_config["IMG_SIZE"] = hyperparams["IMG_SIZE"]

    log_dir = os.path.join("exp", datetime.now().strftime("%Y-%m-%d_%H-%M-%S"))
    
    model_instance = Model(model_config, verbose=False)
    macs = calc_macs(model_instance.model, (3, data_config["IMG_SIZE"], data_config["IMG_SIZE"]))
    
    if trial.number > 1:
        if success:
            if macs > before_macs:
                print(f' trial: {trial.number}, I want to search lower macs: now {macs} >>> before {before_macs}')
                raise optuna.structs.TrialPruned()
    
    if macs>1000000.0:      ########
        print(f' trial: {trial.number}, This model has very large macs:{macs}')
        success = False
        raise optuna.structs.TrialPruned()##############
    
    
    os.makedirs(log_dir, exist_ok=True)
    
    # model_config, data_config
    _, best_f1 = train(
        model_config=model_config,
        data_config=data_config,
        log_dir=log_dir,
        fp16=data_config["FP16"],
        device=device,
    )
    
    before_macs = macs
    success = True

    return best_f1, macs

## performance comparison by loss

In [33]:
model_config = read_yaml(cfg="exp/0.5177_100epoch_1120/model.yml")
data_config = read_yaml(cfg="exp/0.5177_100epoch_1120/data.yml")

In [34]:
log_dir = os.path.join("exp", datetime.now().strftime("%Y-%m-%d_%H-%M-%S"))
os.makedirs(log_dir, exist_ok=True)

In [8]:
#cross entropy
best_f1, best_acc = train(
        model_config=model_config,
        data_config=data_config,
        log_dir=log_dir,
        fp16=data_config["FP16"],
        device=device,
    )

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'Hardswish'] |            3           16
  1 |   2 |        864 |          DWConv | [16, 5, 2, None, 'Hardswish'] |           16           16
  2 |   3 |        144 |          DWConv | [16, 1, 2, None, 'Hardswish'] |           16           16
  3 |   2 |     19,080 | InvertedResidualv3 | [5, 2.9, 32, 1, 0, 2] |           16           32
  4 |   2 |     38,000 | InvertedResidualv3 | [3, 4.6, 48, 0, 1, 1] |           32           48
  5 |   1 |     38,400 |            Conv |          [768, 1, 1] |           48          768
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          768          768
  7 |   1 |      6,930 |       FixedConv | [9, 1, 1, None, 1, None] |          768            9
Model Summary: 90 layers, 103,882 p


Model saved. Current best test f1: 0.092



Model saved. Current best test f1: 0.120



Model saved. Current best test f1: 0.159



Model saved. Current best test f1: 0.164


...


Model saved. Current best test f1: 0.370



Model saved. Current best test f1: 0.377



Model saved. Current best test f1: 0.386



Model saved. Current best test f1: 0.389



Model saved. Current best test f1: 0.393


In [7]:
#adjustment loss
best_f1, best_acc = train(
        model_config=model_config,
        data_config=data_config,
        log_dir=log_dir,
        fp16=data_config["FP16"],
        device=device,
    )

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'Hardswish'] |            3           16
  1 |   2 |        864 |          DWConv | [16, 5, 2, None, 'Hardswish'] |           16           16
  2 |   3 |        144 |          DWConv | [16, 1, 2, None, 'Hardswish'] |           16           16
  3 |   2 |     19,080 | InvertedResidualv3 | [5, 2.9, 32, 1, 0, 2] |           16           32
  4 |   2 |     38,000 | InvertedResidualv3 | [3, 4.6, 48, 0, 1, 1] |           32           48
  5 |   1 |     38,400 |            Conv |          [768, 1, 1] |           48          768
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          768          768
  7 |   1 |      6,930 |       FixedConv | [9, 1, 1, None, 1, None] |          768            9
Model Summary: 90 layers, 103,882 p


Model saved. Current best test f1: 0.134



Model saved. Current best test f1: 0.150



Model saved. Current best test f1: 0.152



Model saved. Current best test f1: 0.153


...


Model saved. Current best test f1: 0.348



Model saved. Current best test f1: 0.349



Model saved. Current best test f1: 0.349



Model saved. Current best test f1: 0.354



Model saved. Current best test f1: 0.363


In [8]:
data_config['EPOCHS']=200

In [9]:
#custom loss
best_f1, best_acc = train(
        model_config=model_config,
        data_config=data_config,
        log_dir=log_dir,
        fp16=data_config["FP16"],
        device=device,
    )

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'Hardswish'] |            3           16
  1 |   2 |        864 |          DWConv | [16, 5, 2, None, 'Hardswish'] |           16           16
  2 |   3 |        144 |          DWConv | [16, 1, 2, None, 'Hardswish'] |           16           16
  3 |   2 |     19,080 | InvertedResidualv3 | [5, 2.9, 32, 1, 0, 2] |           16           32
  4 |   2 |     38,000 | InvertedResidualv3 | [3, 4.6, 48, 0, 1, 1] |           32           48
  5 |   1 |     38,400 |            Conv |          [768, 1, 1] |           48          768
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          768          768
  7 |   1 |      6,930 |       FixedConv | [9, 1, 1, None, 1, None] |          768            9
Model Summary: 90 layers, 103,882 p


Model saved. Current best test f1: 0.116



Model saved. Current best test f1: 0.127



Model saved. Current best test f1: 0.143



Model saved. Current best test f1: 0.160


...


Model saved. Current best test f1: 0.457



Model saved. Current best test f1: 0.462



Model saved. Current best test f1: 0.464



Model saved. Current best test f1: 0.470



Model saved. Current best test f1: 0.475


In [9]:
data_config['EPOCHS']=200

In [10]:
#weighted_cross_entropy
best_f1, best_acc = train(
        model_config=model_config,
        data_config=data_config,
        log_dir=log_dir,
        fp16=data_config["FP16"],
        device=device,
    )

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'ReLU'] |            3           16
  1 |   1 |      3,392 | InvertedResidualv3 | [3, 3.0, 40, 0, 1, 2] |           16           40
  2 |   2 |        160 |          DWConv | [16, 1, 2, None, 'ReLU'] |           40           16
  3 |   1 |      2,304 |            Conv |          [128, 1, 1] |           16          128
  4 |   1 |          0 |   GlobalAvgPool |                   [] |          128          128
  5 |   1 |      1,170 |       FixedConv | [9, 1, 1, None, 1, None] |          128            9
Model Summary: 35 layers, 7,490 parameters, 7,490 gradients
Model save path: exp/2021-06-03_13-10-02/best.pt
macs: 4920210.0
train 200 epochs this model!



Model saved. Current best test f1: 0.163



Model saved. Current best test f1: 0.194



Model saved. Current best test f1: 0.207



Model saved. Current best test f1: 0.233


...


Model saved. Current best test f1: 0.368



Model saved. Current best test f1: 0.374



Model saved. Current best test f1: 0.378



Model saved. Current best test f1: 0.379



Model saved. Current best test f1: 0.382


In [12]:
data_config['EPOCHS']=50

In [16]:
#weighted_cross_entropy retraining
best_f1, best_acc = train(
        model_config=model_config,
        data_config=data_config,
        log_dir=log_dir,
        fp16=data_config["FP16"],
        device=device,
    )

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'ReLU'] |            3           16
  1 |   1 |      3,392 | InvertedResidualv3 | [3, 3.0, 40, 0, 1, 2] |           16           40
  2 |   2 |        160 |          DWConv | [16, 1, 2, None, 'ReLU'] |           40           16
  3 |   1 |      2,304 |            Conv |          [128, 1, 1] |           16          128
  4 |   1 |          0 |   GlobalAvgPool |                   [] |          128          128
  5 |   1 |      1,170 |       FixedConv | [9, 1, 1, None, 1, None] |          128            9
Model Summary: 35 layers, 7,490 parameters, 7,490 gradients
Model save path: exp/2021-06-04_00-16-35/best.pt
macs: 4920210.0
train 50 epochs this model!



Model saved. Current best test f1: 0.356



Model saved. Current best test f1: 0.359



Model saved. Current best test f1: 0.361


KeyboardInterrupt: 

## define optuna study class create function

In [10]:
def tune(gpu_id: int, storage: Union[str, None] = None, study_name: str = "pstage_automl"):
    if not torch.cuda.is_available():
        device = torch.device("cpu")
    elif 0 <= gpu_id < torch.cuda.device_count():
        device = torch.device(f"cuda:{gpu_id}")
    sampler = optuna.samplers.MOTPESampler(n_startup_trials=20)
    if storage is not None:
        rdb_storage = optuna.storages.RDBStorage(url=storage)
    else:
        rdb_storage = None

    study = optuna.create_study(
        directions=["maximize", "minimize"],
        storage=rdb_storage,
        study_name=study_name,
        sampler=sampler,
        load_if_exists=True
    )
    study.optimize(lambda trial: objective(trial, device), n_trials=3000)

    pruned_trials = [
        t for t in study.trials if t.state == optuna.trial.TrialState.PRUNED
    ]
    complete_trials = [
        t for t in study.trials if t.state == optuna.trial.TrialState.COMPLETE
    ]

    print("Study statistics: ")
    print("  Number of finished trials: ", len(study.trials))
    print("  Number of pruned trials: ", len(pruned_trials))
    print("  Number of complete trials: ", len(complete_trials))

    print("Best trials:")
    best_trials = study.best_trials

    ## trials that satisfies Pareto Fronts
    for tr in best_trials:
        print(f"  value1:{tr.values[0]}, value2:{tr.values[1]}")
        for key, value in tr.params.items():
            print(f"    {key}:{value}")

    best_trial = get_best_trial_with_condition(study)

In [12]:
#experiment1

gpu_id=0

storage=""

study_name="pstage_automl"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-05-31 20:46:39,247] A new study created in memory with name: pstage_automl


idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'Hardswish'] |            3           16
  1 |   1 |      2,336 |            Conv | [16, 3, 2, None, 1, 'Hardswish'] |           16           16
  2 |   2 |     11,136 |            Conv | [96, 1, 2, None, 1, 'ReLU'] |           16           96
  3 |   4 |     67,744 | InvertedResidualv2 |          [128, 1, 2] |           96          128
  4 |   3 |    310,400 | InvertedResidualv2 |           [64, 7, 1] |          128           64
  5 |   1 |     50,688 |            Conv |          [768, 1, 1] |           64          768
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          768          768
  7 |   1 |      6,930 |       FixedConv | [9, 1, 1, None, 1, None] |          768            9
Model Summary: 97 layers, 449,698 pa


Model saved. Current best test f1: 0.134



Model saved. Current best test f1: 0.153



Model saved. Current best test f1: 0.230


...


Model saved. Current best test f1: 0.170



Model saved. Current best test f1: 0.181



Model saved. Current best test f1: 0.198



Model saved. Current best test f1: 0.214


KeyboardInterrupt: 

In [15]:
#experiment2

gpu_id=0

storage=""

study_name="pstage_automl2"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-05-31 23:51:28,450] A new study created in memory with name: pstage_automl2
[I 2021-05-31 23:51:39,635] Trial 0 pruned. 


 trial: 0, This model has very large macs:22418694154.0


[I 2021-05-31 23:51:39,982] Trial 1 pruned. 
[I 2021-05-31 23:51:40,066] Trial 2 pruned. 


 trial: 1, This model has very large macs:2684199146.0
 trial: 2, This model has very large macs:97575570.0


[I 2021-05-31 23:51:40,325] Trial 3 pruned. 


...


Model saved. Current best test f1: 0.219



Model saved. Current best test f1: 0.248



Model saved. Current best test f1: 0.287


Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f5f83207b80>
Traceback (most recent call last):
  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1101, in __del__
    self._shutdown_workers()
  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1075, in _shutdown_workers
Exception ignored in:     <function _MultiProcessingDataLoaderIter.__del__ at 0x7f5f83207b80>w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)
Traceback (most recent call last):

  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1101, in __del__
  File "/miniconda/lib/python3.8/multiprocessing/process.py", line 147, in join
        self._shutdown_workers()assert self._parent_pid == os.getpid(), 'can only join a child process'

  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1075, in _shutdown_workers
AssertionError    : w.join(timeout=_utils.MP_STATUS_CHEC

KeyboardInterrupt: 

In [16]:
#experiment3

gpu_id=0

storage=""

study_name="pstage_automl3"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-01 01:08:09,331] A new study created in memory with name: pstage_automl3
[I 2021-06-01 01:08:09,458] Trial 0 pruned. 


 trial: 0, This model has very large macs:547851490.0


[I 2021-06-01 01:08:10,133] Trial 1 pruned. 
[I 2021-06-01 01:08:10,216] Trial 2 pruned. 


 trial: 1, This model has very large macs:16692194322.0
 trial: 2, This model has very large macs:330089306.0


[I 2021-06-01 01:08:10,837] Trial 3 pruned. 


...


Model saved. Current best test f1: 0.232



Model saved. Current best test f1: 0.248



Model saved. Current best test f1: 0.252



Model saved. Current best test f1: 0.258


KeyboardInterrupt: 

In [19]:
#experiment4

gpu_id=0

storage=""

study_name="pstage_automl4"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-01 10:43:22,377] A new study created in memory with name: pstage_automl4
[I 2021-06-01 10:43:22,840] Trial 0 pruned. 


 trial: 0, This model has very large macs:4846663330.0


[I 2021-06-01 10:43:23,150] Trial 1 pruned. 


 trial: 1, This model has very large macs:4702458674.0


[I 2021-06-01 10:43:24,488] Trial 2 pruned. 
[I 2021-06-01 10:43:24,619] Trial 3 pruned. 


...

 trial: 90, This model has very large macs:6730926354.0
 trial: 91, This model has very large macs:1995367026.0


[I 2021-06-02 00:19:35,781] Trial 92 pruned. 


 trial: 92, This model has very large macs:2018815314.0
idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |            Conv | [16, 3, 2, None, 1, 'ReLU'] |            3           16
  1 |   3 |      1,584 |          DWConv | [48, 3, 1, None, 'Hardswish'] |           16           48
  2 |   3 |     22,008 | InvertedResidualv3 | [5, 4.5, 8, 0, 0, 2] |           48            8
  3 |   4 |      7,680 |            Conv | [48, 1, 2, None, 1, 'ReLU'] |            8           48
  4 |   1 |     25,136 | InvertedResidualv2 |          [112, 3, 2] |           48          112
  5 |   1 |     14,592 |            Conv |          [128, 1, 1] |          112          128
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          128          128
  7 |   1 |      1,170 |       FixedConv | [9, 1, 1, None, 1, None] |          12


Model saved. Current best test f1: 0.108


KeyboardInterrupt: 

In [19]:
#experiment5

gpu_id=0

storage=""

study_name="pstage_automl5"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-02 01:41:18,995] A new study created in memory with name: pstage_automl5
[I 2021-06-02 01:41:19,167] Trial 0 pruned. 
[I 2021-06-02 01:41:19,274] Trial 1 pruned. 


 trial: 0, This model has very large macs:10330538946.0
 trial: 1, This model has very large macs:1492541074.0


[I 2021-06-02 01:41:19,487] Trial 2 pruned. 
[I 2021-06-02 01:41:19,566] Trial 3 pruned. 


 trial: 2, This model has very large macs:6712351506.0
 trial: 3, This model has very large macs:1548414834.0


[I 2021-06-02 01:41:19,696] Trial 4 pruned. 
[I 2021-06-02 01:41:19,857] Trial 5 pruned. 


...

 trial: 749, This model has very large macs:5009040498.0
 trial: 750, This model has very large macs:1540432818.0


[I 2021-06-02 01:43:14,896] Trial 751 pruned. 


 trial: 751, This model has very large macs:141493266.0
idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |            Conv | [16, 3, 2, None, 1, 'Hardswish'] |            3           16
  1 |   5 |      2,320 | InvertedResidualv2 |           [16, 1, 2] |           16           16
  2 |   3 |      4,224 |          DWConv | [128, 3, 2, None, 'ReLU'] |           16          128
  3 |   2 |      1,536 |          DWConv | [256, 1, 2, None, 'Hardswish'] |          128          256
  4 |   4 |      4,800 |          DWConv | [320, 1, 2, None, 'Hardswish'] |          256          320
  5 |   1 |    206,080 |            Conv | [640, 1, 1, None, 1, 'Hardswish'] |          320          640
  6 |   1 |     82,176 |            Conv |          [128, 1, 1] |          640          128
  7 |   1 |          0 |   GlobalAvgPool |               


Model saved. Current best test f1: 0.083


KeyboardInterrupt: 

In [22]:
#experiment6

gpu_id=0

storage=""

study_name="pstage_automl6"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-02 02:35:07,884] A new study created in memory with name: pstage_automl6
[I 2021-06-02 02:35:08,005] Trial 0 pruned. 
[I 2021-06-02 02:35:08,104] Trial 1 pruned. 
[I 2021-06-02 02:35:08,187] Trial 2 pruned. 


 trial: 0, This model has very large macs:325224202.0
 trial: 1, This model has very large macs:1943149066.0
 trial: 2, This model has very large macs:620069906.0


[I 2021-06-02 02:35:08,298] Trial 3 pruned. 
[I 2021-06-02 02:35:08,404] Trial 4 pruned. 


 trial: 3, This model has very large macs:1016422258.0
 trial: 4, This model has very large macs:882466770.0


[I 2021-06-02 02:35:08,922] Trial 5 pruned. 
[I 2021-06-02 02:35:09,061] Trial 6 pruned. 


...

 trial: 1448, This model has very large macs:20841845186.0


[I 2021-06-02 02:38:50,827] Trial 1449 pruned. 
[I 2021-06-02 02:38:50,916] Trial 1450 pruned. 


 trial: 1449, This model has very large macs:14983256354.0
 trial: 1450, This model has very large macs:456995050.0
idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |          DWConv | [16, 3, 2, None, 'Hardswish'] |            3           16
  1 |   2 |        864 |          DWConv | [16, 5, 2, None, 'Hardswish'] |           16           16
  2 |   3 |        144 |          DWConv | [16, 1, 2, None, 'Hardswish'] |           16           16
  3 |   2 |     19,080 | InvertedResidualv3 | [5, 2.9, 32, 1, 0, 2] |           16           32
  4 |   2 |     38,000 | InvertedResidualv3 | [3, 4.6, 48, 0, 1, 1] |           32           48
  5 |   1 |     38,400 |            Conv |          [768, 1, 1] |           48          768
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          768          768
  7 |   1 |    


Model saved. Current best test f1: 0.080


KeyboardInterrupt: 

In [23]:
#experiment7

gpu_id=0

storage=""

study_name="pstage_automl7"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-03 12:19:48,498] A new study created in memory with name: pstage_automl7
[I 2021-06-03 12:19:48,579] Trial 0 pruned. 
[I 2021-06-03 12:19:48,656] Trial 1 pruned. 
[I 2021-06-03 12:19:48,766] Trial 2 pruned. 


 trial: 0, This model has very large macs:333132130.0
 trial: 1, This model has very large macs:495217858.0
 trial: 2, This model has very large macs:922309650.0


[I 2021-06-03 12:19:48,873] Trial 3 pruned. 
[I 2021-06-03 12:19:48,935] Trial 4 pruned. 


 trial: 3, This model has very large macs:1297698234.0
 trial: 4, This model has very large macs:65548042.0


[I 2021-06-03 12:19:49,183] Trial 5 pruned. 
[I 2021-06-03 12:19:49,226] Trial 6 pruned. 


...

[I 2021-06-03 12:25:18,187] Trial 1995 pruned. 
[I 2021-06-03 12:25:18,373] Trial 1996 pruned. 


 trial: 1995, This model has very large macs:3065667226.0
 trial: 1996, This model has very large macs:2409540706.0


[I 2021-06-03 12:25:18,674] Trial 1997 pruned. 
[I 2021-06-03 12:25:18,750] Trial 1998 pruned. 
[I 2021-06-03 12:25:18,854] Trial 1999 pruned. 


 trial: 1997, This model has very large macs:6875133914.0
 trial: 1998, This model has very large macs:110503410.0
 trial: 1999, This model has very large macs:569713554.0
Study statistics: 
  Number of finished trials:  2000
  Number of pruned trials:  2000
  Number of complete trials:  0
Best trials:


NameError: name 'get_best_trial_with_condition' is not defined

In [24]:
#experiment8

gpu_id=0

storage=""

study_name="pstage_automl8"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-04 02:40:25,646] A new study created in memory with name: pstage_automl8
[I 2021-06-04 02:40:25,813] Trial 0 pruned. 
[I 2021-06-04 02:40:25,857] Trial 1 pruned. 
[I 2021-06-04 02:40:25,939] Trial 2 pruned. 
[I 2021-06-04 02:40:25,987] Trial 3 pruned. 


 trial: 0, This model has very large macs:5539770754.0
 trial: 1, This model has very large macs:141459802.0
 trial: 2, This model has very large macs:968465002.0
 trial: 3, This model has very large macs:864189330.0


[I 2021-06-04 02:40:26,057] Trial 4 pruned. 
[I 2021-06-04 02:40:26,114] Trial 5 pruned. 


 trial: 4, This model has very large macs:1159774994.0
 trial: 5, This model has very large macs:2295520146.0


[I 2021-06-04 02:40:26,429] Trial 6 pruned. 
[I 2021-06-04 02:40:26,498] Trial 7 pruned. 
[I 2021-06-04 02:40:26,554] Trial 8 pruned. 


...


Model saved. Current best test f1: 0.178



Model saved. Current best test f1: 0.206



Model saved. Current best test f1: 0.255



Model saved. Current best test f1: 0.296


KeyboardInterrupt: 

In [14]:
#experiment9

gpu_id=0

storage=""

study_name="pstage_automl9"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-04 12:04:17,033] A new study created in memory with name: pstage_automl9
[I 2021-06-04 12:04:17,529] Trial 0 pruned. 


 trial: 0, This model has very large macs:47744379922.0


[I 2021-06-04 12:04:17,849] Trial 1 pruned. 


 trial: 1, This model has very large macs:13226395922.0


[I 2021-06-04 12:04:18,148] Trial 2 pruned. 
[I 2021-06-04 12:04:18,224] Trial 3 pruned. 
[I 2021-06-04 12:04:18,316] Trial 4 pruned. 


...

[I 2021-06-04 22:31:46,876] Trial 497 pruned. 
[I 2021-06-04 22:31:47,000] Trial 498 pruned. 


 trial: 497, I want to search lower macs: now 9834232378.0 >>> before 59366202.0
 trial: 498, I want to search lower macs: now 1175477778.0 >>> before 59366202.0


[I 2021-06-04 22:31:47,265] Trial 499 pruned. 


 trial: 499, I want to search lower macs: now 16622544690.0 >>> before 59366202.0
Study statistics: 
  Number of finished trials:  500
  Number of pruned trials:  499
  Number of complete trials:  1
Best trials:
  value1:0.6612665684830633, value2:59366202.0
    epochs:150
    n_select:6
    batch_size:64
    m1:DWConv
    m1/repeat:1
    m1/out_channels:48
    m1/stride:2
    m1/activation:ReLU
    m2:DWConv
    m2/repeat:4
    m2/out_channels:16
    m2/stride:2
    m2/kernel_size:3
    m2/activation:Hardswish
    m3:Conv
    m3/repeat:4
    m3/stride:2
    m3/out_channels:32
    m3/kernel_size:1
    m3/activation:ReLU
    m4:Pass
    m4/repeat:4
    m4/stride:2
    m5:Pass
    m5/repeat:3
    m6:Pass
    m6/repeat:5
    m6/stride:2
    m7:InvertedResidualv3
    m7/repeat:2
    m7/stride:2
    m7/kernel_size:5
    m7/v3_t:2.8
    m7/v3_c:88
    m7/v3_se:1
    m7/v3_hs:0
    last_dim:1024


NameError: name 'get_best_trial_with_condition' is not defined

In [16]:
#experiment10

gpu_id=0

storage=""

study_name="pstage_automl10"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-04 22:42:15,267] A new study created in memory with name: pstage_automl10
[I 2021-06-04 22:42:15,378] Trial 0 pruned. 
[I 2021-06-04 22:42:15,526] Trial 1 pruned. 


 trial: 0, This model has very large macs:698105250.0
 trial: 1, This model has very large macs:3141018770.0


[I 2021-06-04 22:42:15,635] Trial 2 pruned. 
[I 2021-06-04 22:42:15,765] Trial 3 pruned. 


 trial: 2, This model has very large macs:1359935922.0
 trial: 3, This model has very large macs:1915878290.0


[I 2021-06-04 22:42:16,253] Trial 4 pruned. 
[I 2021-06-04 22:42:16,411] Trial 5 pruned. 


...

[I 2021-06-05 01:46:45,578] Trial 497 pruned. 
[I 2021-06-05 01:46:45,686] Trial 498 pruned. 


 trial: 497, I want to search lower macs: now 3119549202.0 >>> before 48317522.0
 trial: 498, I want to search lower macs: now 397282178.0 >>> before 48317522.0


[I 2021-06-05 01:46:46,006] Trial 499 pruned. 


 trial: 499, I want to search lower macs: now 10837925930.0 >>> before 48317522.0
Study statistics: 
  Number of finished trials:  500
  Number of pruned trials:  499
  Number of complete trials:  1
Best trials:
  value1:0.6169612174766814, value2:48317522.0
    epochs:50
    n_select:0
    batch_size:16
    m1:DWConv
    m1/repeat:1
    m1/out_channels:32
    m1/stride:2
    m1/activation:Hardswish
    m2:Conv
    m2/repeat:3
    m2/out_channels:32
    m2/stride:2
    m2/kernel_size:1
    m2/activation:Hardswish
    m3:Pass
    m3/repeat:3
    m3/stride:2
    m4:InvertedResidualv2
    m4/repeat:4
    m4/stride:2
    m4/v2_c:16
    m4/v2_t:1
    m5:Pass
    m5/repeat:1
    m6:DWConv
    m6/repeat:2
    m6/stride:2
    m6/out_channels:80
    m6/kernel_size:5
    m6/activation:Hardswish
    m7:Pass
    m7/repeat:4
    m7/stride:1
    last_dim:128


NameError: name 'get_best_trial_with_condition' is not defined

In [27]:
#experiment11

gpu_id=0

storage=""

study_name="pstage_automl11"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-05 21:36:08,489] A new study created in memory with name: pstage_automl11
[I 2021-06-05 21:36:08,770] Trial 0 pruned. 
[I 2021-06-05 21:36:08,883] Trial 1 pruned. 


 trial: 0, This model has very large macs:2809145618.0
 trial: 1, This model has very large macs:1988728082.0


[I 2021-06-05 21:36:08,991] Trial 2 pruned. 


 trial: 2, This model has very large macs:479419650.0


[I 2021-06-05 21:36:09,234] Trial 3 pruned. 


...

[I 2021-06-06 10:04:03,517] Trial 498 pruned. 


 trial: 498, I want to search lower macs: now 14184399506.0 >>> before 54645042.0


[I 2021-06-06 10:04:04,439] Trial 499 pruned. 


 trial: 499, I want to search lower macs: now 23287239314.0 >>> before 54645042.0
Study statistics: 
  Number of finished trials:  500
  Number of pruned trials:  499
  Number of complete trials:  1
Best trials:
  value1:0.6794305351006382, value2:54645042.0
    n_select:2
    batch_size:64
    m1:Conv
    m1/repeat:1
    m1/out_channels:64
    m1/stride:2
    m1/activation:Hardswish
    m2:InvertedResidualv2
    m2/repeat:4
    m2/out_channels:32
    m2/stride:2
    m2/v2_c:32
    m2/v2_t:1
    m3:Pass
    m3/repeat:2
    m3/stride:2
    m4:Conv
    m4/repeat:4
    m4/stride:2
    m4/out_channels:16
    m4/kernel_size:1
    m4/activation:ReLU
    m5:InvertedResidualv2
    m5/repeat:1
    m5/v2_c:48
    m5/v2_t:2
    m5/stride:2
    m6:InvertedResidualv3
    m6/repeat:5
    m6/stride:2
    m6/kernel_size:3
    m6/v3_t:1.4
    m6/v3_c:48
    m6/v3_se:0
    m6/v3_hs:0
    m7:Pass
    m7/repeat:5
    m7/stride:1
    last_dim:896


NameError: name 'get_best_trial_with_condition' is not defined

In [30]:
#experiment12

gpu_id=0

storage=""

study_name="pstage_automl12"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-06 10:11:20,249] A new study created in memory with name: pstage_automl12
[I 2021-06-06 10:11:20,382] Trial 0 pruned. 


 trial: 0, This model has very large macs:1047126114.0


[I 2021-06-06 10:11:20,775] Trial 1 pruned. 


 trial: 1, This model has very large macs:8021693074.0


[I 2021-06-06 10:11:21,197] Trial 2 pruned. 
[I 2021-06-06 10:11:21,385] Trial 3 pruned. 


...

[I 2021-06-07 06:00:01,995] Trial 498 pruned. 


 trial: 498, I want to search lower macs: now 17054165482.0 >>> before 53292690.0


[I 2021-06-07 06:00:03,251] Trial 499 pruned. 


 trial: 499, I want to search lower macs: now 9033997330.0 >>> before 53292690.0
Study statistics: 
  Number of finished trials:  500
  Number of pruned trials:  499
  Number of complete trials:  1
Best trials:
  value1:0.7063082965144821, value2:53292690.0
    n_select:6
    batch_size:48
    m1:Conv
    m1/repeat:1
    m1/out_channels:16
    m1/stride:2
    m1/activation:Hardswish
    m2:InvertedResidualv2
    m2/repeat:5
    m2/out_channels:128
    m2/stride:2
    m2/v2_c:32
    m2/v2_t:1
    m3:DWConv
    m3/repeat:2
    m3/stride:2
    m3/out_channels:48
    m3/kernel_size:3
    m3/activation:ReLU
    m4:Pass
    m4/repeat:4
    m4/stride:1
    m5:InvertedResidualv3
    m5/repeat:2
    m5/kernel_size:3
    m5/v3_t:5.0
    m5/v3_c:48
    m5/v3_se:0
    m5/v3_hs:0
    m5/stride:2
    m6:Pass
    m6/repeat:5
    m6/stride:2
    m7:Pass
    m7/repeat:1
    m7/stride:1
    last_dim:640


NameError: name 'get_best_trial_with_condition' is not defined

In [32]:
#experiment13

gpu_id=0

storage=""

study_name="pstage_automl13"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-07 07:44:35,504] A new study created in memory with name: pstage_automl13
[I 2021-06-07 07:44:35,858] Trial 0 pruned. 


 trial: 0, This model has very large macs:375023410.0


[I 2021-06-07 07:44:36,697] Trial 1 pruned. 


 trial: 1, This model has very large macs:3393945538.0


[I 2021-06-07 07:44:37,549] Trial 2 pruned. 


...

[I 2021-06-07 07:53:45,655] Trial 498 pruned. 


 trial: 498, This model has very large macs:137135106522.0


[I 2021-06-07 07:53:46,984] Trial 499 pruned. 


 trial: 499, This model has very large macs:19723482586.0
Study statistics: 
  Number of finished trials:  500
  Number of pruned trials:  500
  Number of complete trials:  0
Best trials:


NameError: name 'get_best_trial_with_condition' is not defined

In [12]:
#experiment14

gpu_id=0

storage=""

study_name="pstage_automl14"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-11 20:23:43,754] A new study created in memory with name: pstage_automl14
[I 2021-06-11 20:23:44,467] Trial 0 pruned. 


 trial: 0, This model has very large macs:209369466.0


[I 2021-06-11 20:23:45,014] Trial 1 pruned. 


 trial: 1, This model has very large macs:408898090.0


[I 2021-06-11 20:23:45,539] Trial 2 pruned. 


...


Model saved. Current best test f1: 0.340



Model saved. Current best test f1: 0.348



Model saved. Current best test f1: 0.357



Model saved. Current best test f1: 0.372


KeyboardInterrupt: 

In [11]:
#experiment15

gpu_id=0

storage=""

study_name="pstage_automl15"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-11 23:03:47,399] A new study created in memory with name: pstage_automl15
[I 2021-06-11 23:03:47,708] Trial 0 pruned. 


 trial: 0, This model has very large macs:356096074.0


[I 2021-06-11 23:03:48,023] Trial 1 pruned. 


 trial: 1, This model has very large macs:294094098.0


[I 2021-06-11 23:03:48,278] Trial 2 pruned. 


...


Model saved. Current best test f1: 0.438



Model saved. Current best test f1: 0.442



Model saved. Current best test f1: 0.449



Model saved. Current best test f1: 0.454


KeyboardInterrupt: 

In [29]:
#experiment16

gpu_id=0

storage=""

study_name="pstage_automl16"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-13 08:05:21,021] A new study created in memory with name: pstage_automl16


idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   3 |     75,840 |            Conv | [64, 3, 1, None, 1, 'Hardswish'] |            3           64
  1 |   1 |      8,160 |          DWConv | [80, 5, 2, None, 'ReLU'] |           64           80
  2 |   4 |    121,504 | InvertedResidualv3 | [5, 6.0, 32, 0, 1, 2] |           80           32
  3 |   2 |    387,840 |            Conv | [192, 3, 1, None, 1, 'ReLU'] |           32          192
  4 |   2 |    215,424 | InvertedResidualv2 |           [48, 4, 2] |          192           48
  5 |   5 |    169,024 | InvertedResidualv2 |           [64, 4, 1] |           48           64
  6 |   5 | 81,724,160 |            Conv | [896, 5, 2, None, 1, 'Hardswish'] |           64          896
  7 |   1 |    574,720 |            Conv |          [640, 1, 1] |          896          640
  8 |   1 |          0 |   


Model saved. Current best test f1: 0.096



Model saved. Current best test f1: 0.120



Model saved. Current best test f1: 0.150


...

[I 2021-06-14 03:25:31,048] Trial 0 finished with values: [0.7302405498281787, 10820041362.0] and parameters: {'n_select': 6, 'batch_size': 48, 'm1': 'Conv', 'm1/repeat': 3, 'm1/out_channels': 64, 'm1/stride': 1, 'm1/activation': 'Hardswish', 'm2': 'DWConv', 'm2/repeat': 1, 'm2/out_channels': 80, 'm2/stride': 2, 'm2/kernel_size': 5, 'm2/activation': 'ReLU', 'm3': 'InvertedResidualv3', 'm3/repeat': 4, 'm3/stride': 2, 'm3/kernel_size': 5, 'm3/v3_t': 6.0, 'm3/v3_c': 32, 'm3/v3_se': 0, 'm3/v3_hs': 1, 'm4': 'Conv', 'm4/repeat': 2, 'm4/stride': 1, 'm4/out_channels': 192, 'm4/kernel_size': 3, 'm4/activation': 'ReLU', 'm5': 'InvertedResidualv2', 'm5/repeat': 2, 'm5/v2_c': 48, 'm5/v2_t': 4, 'm5/stride': 2, 'm6': 'InvertedResidualv2', 'm6/repeat': 5, 'm6/stride': 1, 'm6/v2_c': 64, 'm6/v2_t': 4, 'm7': 'Conv', 'm7/repeat': 5, 'm7/stride': 2, 'm7/out_channels': 896, 'm7/kernel_size': 5, 'm7/activation': 'Hardswish', 'last_dim': 640}. 



idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   2 |      1,056 |          DWConv | [48, 3, 2, None, 'ReLU'] |            3           48
  1 |   4 |      1,984 |          DWConv | [32, 3, 2, None, 'ReLU'] |           48           32
  2 |   4 |  1,332,224 |            Conv | [128, 5, 2, None, 1, 'ReLU'] |           32          128
  3 |   5 |      7,872 |          DWConv | [96, 3, 1, None, 'Hardswish'] |          128           96
  4 |   4 |     14,544 | InvertedResidualv2 |           [48, 1, 1] |           96           48
  5 |   2 |    964,288 |            Conv | [304, 3, 1, None, 1, 'ReLU'] |           48          304
  6 |   3 |  1,285,200 | InvertedResidualv2 |          [112, 7, 2] |          304          112
  7 |   1 |    116,736 |            Conv |         [1024, 1, 1] |          112         1024
  8 |   1 |          0 |   GlobalA


Model saved. Current best test f1: 0.093



Model saved. Current best test f1: 0.137


KeyboardInterrupt: 

In [11]:
#experiment17

gpu_id=0

storage=""

study_name="pstage_automl17"

tune(gpu_id, storage=None if storage == "" else storage, study_name=study_name)

[I 2021-06-14 15:59:56,973] A new study created in memory with name: pstage_automl17
[I 2021-06-14 15:59:57,186] Trial 0 pruned. 
[I 2021-06-14 15:59:57,283] Trial 1 pruned. 
[I 2021-06-14 15:59:57,335] Trial 2 pruned. 
[I 2021-06-14 15:59:57,380] Trial 3 pruned. 


 trial: 0, This model has very large macs:1178958714.0
 trial: 1, This model has very large macs:65471418.0
 trial: 2, This model has very large macs:198122706.0
 trial: 3, This model has very large macs:16364026.0


[I 2021-06-14 15:59:57,529] Trial 4 pruned. 
[I 2021-06-14 15:59:57,568] Trial 5 pruned. 
[I 2021-06-14 15:59:57,618] Trial 6 pruned. 
[I 2021-06-14 15:59:57,666] Trial 7 pruned. 
[I 2021-06-14 15:59:57,704] Trial 8 pruned. 


 trial: 4, This model has very large macs:157272594.0
 trial: 5, This model has very large macs:381605778.0
 trial: 6, This model has very large macs:121814802.0
 trial: 7, This model has very large macs:19262738.0
 trial: 8, This model has very large macs:106017298.0


[I 2021-06-14 15:59:57,947] Trial 9 pruned. 
[I 2021-06-14 15:59:58,007] Trial 10 pruned. 
[I 2021-06-14 15:59:58,070] Trial 11 pruned. 
[I 2021-06-14 15:59:58,105] Trial 12 pruned. 


...

[I 2021-06-14 15:59:58,900] Trial 23 pruned. 
[I 2021-06-14 15:59:58,963] Trial 24 pruned. 
[I 2021-06-14 15:59:59,040] Trial 25 pruned. 


 trial: 23, This model has very large macs:136084434.0
 trial: 24, This model has very large macs:147352722.0
 trial: 25, This model has very large macs:51660946.0


[I 2021-06-14 15:59:59,111] Trial 26 pruned. 
[I 2021-06-14 15:59:59,185] Trial 27 pruned. 
[I 2021-06-14 15:59:59,283] Trial 28 pruned. 


 trial: 26, This model has very large macs:419747346.0
 trial: 27, This model has very large macs:13455370.0
 trial: 28, This model has very large macs:27026578.0
idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |            Conv | [16, 3, 2, None, 1, 'Hardswish'] |            3           16
  1 |   1 |      2,336 |            Conv | [16, 3, 2, None, 1, 'ReLU'] |           16           16
  2 |   1 |      2,336 |            Conv | [16, 3, 2, None, 1, 'ReLU'] |           16           16
  3 |   5 |      1,680 |          DWConv | [112, 1, 2, None, 'ReLU'] |           16          112
  4 |   1 |     12,096 |          DWConv | [448, 5, 1, None, 'ReLU'] |          112          448
  5 |   1 |    403,200 |            Conv |          [896, 1, 1] |          448          896
  6 |   1 |          0 |   GlobalAvgPool |                 

KeyboardInterrupt: 

## define train function

In [1]:
def train(
    model_config: Dict[str, Any],
    data_config: Dict[str, Any],
    log_dir: str,
    fp16: bool,
    device: torch.device,
) -> Tuple[float, float, float]:
    
    
    """Train."""
    # save model_config, data_config
    with open(os.path.join(log_dir, 'data.yml'), 'w') as f:
        yaml.dump(data_config, f, default_flow_style=False)
    with open(os.path.join(log_dir, 'model.yml'), 'w') as f:
        yaml.dump(model_config, f, default_flow_style=False)

   
    #read model_config, create model instance
    model_instance = Model(model_config, verbose=True)
    model_path = os.path.join(log_dir, "best.pt") #best model path
    print(f"Model save path: {model_path}")
    
    #to use GPU
    if os.path.isfile(model_path):
        model_instance.model.load_state_dict(torch.load(model_path, map_location=device))
    model_instance.model.to(device)

    
    # Create dataloader
    train_dl, val_dl, test_dl = create_dataloader(data_config)

    # Calc macs
    macs = calc_macs(model_instance.model, (3, data_config["IMG_SIZE"], data_config["IMG_SIZE"]))
    print(f"macs: {macs}")

    
    # Create optimizer, scheduler, criterion
    #optimizer = torch.optim.SGD(
        #model_instance.model.parameters(), lr=data_config["INIT_LR"]/100, momentum=0.9 
    #)
    
    optimizer = torch.optim.Adam(
        model_instance.model.parameters(), lr=data_config["INIT_LR"]/10000
    )
    
    scheduler = torch.optim.lr_scheduler.OneCycleLR(
        optimizer=optimizer,
        max_lr=data_config["INIT_LR"],
        steps_per_epoch=len(train_dl),
        epochs=data_config["EPOCHS"],
        pct_start=0.05,
    )
    
    #scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=60, eta_min=0)
    
    criterion = CustomCriterion(
        samples_per_cls=get_label_counts(data_config["DATA_PATH"])
        if data_config["DATASET"] == "TACO"
        else None,
        device=device,
    )
    
    # Amp loss scaler
    scaler = (
        torch.cuda.amp.GradScaler() if fp16 and device != torch.device("cpu") else None
    )

    # Create trainer
    trainer = TorchTrainer(
        model=model_instance.model,
        criterion=criterion,
        optimizer=optimizer,
        scheduler=scheduler,
        scaler=scaler,
        device=device,
        model_path=model_path,
        verbose=1,
    )
    
    
    best_acc, best_f1 = trainer.train(
        train_dataloader=train_dl,
        n_epoch=data_config["EPOCHS"],
        val_dataloader=val_dl if val_dl else test_dl,
    )

    
    # evaluate model with test set
    model_instance.model.load_state_dict(torch.load(model_path))
    test_loss, test_f1, test_acc = trainer.test(
        model=model_instance.model, test_dataloader=val_dl if val_dl else test_dl
    )
    
    return test_loss, test_f1, test_acc

NameError: name 'Dict' is not defined

## load configuration file

In [44]:
model_config_path = "exp/0.5177_100epoch_1120/model.yml"
data_config_path = "exp/0.5177_100epoch_1120/data.yml"

model_config = read_yaml(cfg=model_config_path)
data_config = read_yaml(cfg=data_config_path)

In [45]:
data_config

{'AUG_TEST': 'simple_augment_test',
 'AUG_TRAIN': 'randaugment_train',
 'AUG_TRAIN_PARAMS': {'level': None, 'n_select': 2},
 'BATCH_SIZE': 32,
 'DATASET': 'TACO',
 'DATA_PATH': '/opt/ml/input/data/',
 'EPOCHS': 100,
 'FP16': True,
 'IMG_SIZE': 96,
 'INIT_LR': 0.1,
 'VAL_RATIO': 0.0}

In [47]:
model_instance = Model(model_config, verbose=True)

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   3 |        816 |          DWConv | [16, 3, 2, None, 'ReLU'] |            3           16
  1 |   1 |      2,016 | InvertedResidualv2 |           [32, 2, 2] |           16           32
  2 |   4 |      2,288 | InvertedResidualv2 |           [16, 1, 2] |           32           16
  3 |   5 |      7,360 | InvertedResidualv2 |           [16, 2, 2] |           16           16
  4 |   2 |    240,656 | InvertedResidualv3 | [5, 3.5, 128, 1, 1, 2] |           16          128
  5 |   1 |     83,200 |            Conv |          [640, 1, 1] |          128          640
  6 |   1 |          0 |   GlobalAvgPool |                   [] |          640          640
  7 |   1 |      5,778 |       FixedConv | [9, 1, 1, None, 1, None] |          640            9
Model Summary: 161 layers, 342,114 parameters, 342,1

In [48]:
macs = calc_macs(model_instance.model, (3, data_config["IMG_SIZE"], data_config["IMG_SIZE"]))
print(f"macs: {macs}")

macs: 60726258.0


## create log directory

In [164]:
log_dir = os.path.join("exp", datetime.now().strftime("%Y-%m-%d_%H-%M-%S"))
os.makedirs(log_dir, exist_ok=True)

In [165]:
log_dir

'exp/2021-05-31_14-28-17'

## training model

In [167]:
test_loss, test_f1, test_acc = train(
    model_config=model_config,
    data_config=data_config,
    log_dir=log_dir,
    fp16=data_config["FP16"],
    device=device,
)

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |            Conv | [16, 3, 2, None, 1, 'HardSwish'] |            3           16
  1 |   1 |        464 | InvertedResidualv3 |  [3, 1, 16, 0, 0, 1] |           16           16
  2 |   1 |      3,440 | InvertedResidualv3 |  [3, 4, 24, 0, 0, 2] |           16           24
  3 |   1 |      4,440 | InvertedResidualv3 |  [3, 3, 24, 0, 0, 1] |           24           24
  4 |   1 |     10,328 | InvertedResidualv3 |  [5, 3, 40, 1, 0, 2] |           24           40
  5 |   1 |     20,992 | InvertedResidualv3 |  [5, 3, 40, 1, 0, 1] |           40           40
  6 |   1 |     20,992 | InvertedResidualv3 |  [5, 3, 40, 1, 0, 1] |           40           40
  7 |   1 |     32,080 | InvertedResidualv3 |  [3, 6, 80, 0, 1, 2] |           40           80
  8 |   1 |     34,760 | InvertedResidual

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f27849aeb80>
Traceback (most recent call last):
  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1101, in __del__
    self._shutdown_workers()
  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1075, in _shutdown_workers
    w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)
  File "/miniconda/lib/python3.8/multiprocessing/process.py", line 147, in join
    assert self._parent_pid == os.getpid(), 'can only join a child process'
AssertionError: can only join a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f27849aeb80>
Traceback (most recent call last):
  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1101, in __del__
    self._shutdown_workers()
  File "/miniconda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 1075, in _shutdown_workers
Exception 

KeyboardInterrupt: 

## define inference function

In [19]:
#imagefolder function

CLASSES = ['Battery', 'Clothing', 'Glass', 'Metal', 'Paper', 'Paperpack', 'Plastic', 'Plasticbag', 'Styrofoam']

class CustomImageFolder(ImageFolder):
    """ImageFolder with filename."""

    def __getitem__(self, index):
        img_gt = super(CustomImageFolder, self).__getitem__(index)
        fdir = self.imgs[index][0]
        fname = fdir.rsplit(os.path.sep, 1)[-1]
        return (img_gt + (fname,))

In [28]:
#prepare dataloader

def get_dataloader(img_root: str, data_config: str) -> DataLoader:
    """Get dataloader.

    Note:
	Don't forget to set normalization.
    """
    # Load yaml
    data_config = read_yaml(data_config)

    transform_test_args = data_confg["AUG_TEST_PARAMS"] if data_config.get("AUG_TEST_PARAMS") else None
    # Transformation for test
    transform_test = getattr(
        __import__("src.augmentation.policies", fromlist=[""]),
        data_config["AUG_TEST"],
    )(dataset=data_config["DATASET"], img_size=data_config["IMG_SIZE"])

    dataset = CustomImageFolder(root=img_root, transform=transform_test)
    dataloader = DataLoader(
	dataset=dataset,
	batch_size=1,
	num_workers=8
    )
    return dataloader

In [29]:
#define inference function

@torch.no_grad()
def inference(model, dataloader, dst_path: str):
    result = {}
    model = model.to(device)
    model.eval()
    submission_csv = {}
    for img, _, fname in dataloader:
        img = img.to(device)
        pred, enc_data = run_model(model, img)
        pred = torch.argmax(pred)
        submission_csv[fname[0]] = CLASSES[int(pred.detach())]

    result["macs"] = enc_data
    result["submission"] = submission_csv
    j = json.dumps(result, indent=4)
    save_path = os.path.join(dst_path, 'submission.csv')
    with open(save_path, 'w') as outfile:
        json.dump(result, outfile)


## final inference

In [2]:
#prepare path

dst='/opt/ml/'
model_weight = 'exp/2021-05-30_16-41-26/best.pt'
model_config ='exp/2021-05-30_16-41-26/model.yml'
data_config = 'exp/2021-05-30_16-41-26/data.yml'
img_root = 'input/data/test'

In [31]:
# prepare datalaoder
dataloader = get_dataloader(img_root=img_root, data_config=data_config)

# prepare model
model_instance = Model(model_config, verbose=True)
model_instance.model.load_state_dict(torch.load(model_weight, map_location=torch.device('cpu')))

# inference
inference(model_instance.model, dataloader, dst)

idx |   n |     params |          module |            arguments |   in_channel |   out_channel
----------------------------------------------------------------------------------------------
  0 |   1 |        464 |            Conv | [16, 3, 2, None, 1, 'HardSwish'] |            3           16
  1 |   1 |        464 | InvertedResidualv3 |  [3, 1, 16, 0, 0, 1] |           16           16
  2 |   1 |      3,440 | InvertedResidualv3 |  [3, 4, 24, 0, 0, 2] |           16           24
  3 |   1 |      4,440 | InvertedResidualv3 |  [3, 3, 24, 0, 0, 1] |           24           24
  4 |   1 |     10,328 | InvertedResidualv3 |  [5, 3, 40, 1, 0, 2] |           24           40
  5 |   1 |     20,992 | InvertedResidualv3 |  [5, 3, 40, 1, 0, 1] |           40           40
  6 |   1 |     20,992 | InvertedResidualv3 |  [5, 3, 40, 1, 0, 1] |           40           40
  7 |   1 |     32,080 | InvertedResidualv3 |  [3, 6, 80, 0, 1, 2] |           40           80
  8 |   1 |     34,760 | InvertedResidual